# __Volume delay function Study__

![title](img/1.jpg)

In most traffic assignment methods,the effect of road capacity on travel times is specified by means of volume-delay functions t(v) 

which used to express the travel time(or cost) on a road link as a function of the traffic volume v. Usually these functions are expressed as the product of 

the free flow time multiplied by a normalized congestion functionf(x)

__t(v)=t0·f (v/c)__


In order to __update the generalized VDF parameters__, 

a __disaggregated approach__ was developed to __re-evaluate VDF parameters to reflect the characteristics on different segments__.

In [1]:
import numpy as np
import os
import copy
import matplotlib.pyplot as plt
import math
import statistics
from scipy.optimize import curve_fit
import matplotlib.pyplot as plt
import pandas as pd
from random import sample
import warnings
from termcolor import colored
import plotly.express as px
import plotly.offline as pyo
import plotly.graph_objs as go 
import plotly.express as px
from plotly.subplots import make_subplots
pd.set_option('mode.chained_assignment', None)

# A. Global parameter and data input
## A1. Global Parameters
## A2. Data Input
## A3. Data Cleaning and formatting

## A1. Global Parameters

In [2]:
###------------parameters to control trainset size and filter---------###
sample_size = 50 ## sample size for each V/C bin
FF_Condition = 500 ## based on 7 sec headway, 65 mph speed, approximately 500 veh/hr
points_threshold = 100 ## minimal number of data points to calculate FF_SPD for a segment
ffspd_offset = 7 ## free flow speed offset based on post speed when there is not enough data points available
criteria = 'adj_R2 > 0.6 & RMSE < 10' ## Performance Criteria for segment selection
Year_param_emit = [-1] # Years to exclude from dataset
Hour_param_emit = [0,1,2,3,4,19,21,22,23] # Hours to exclude from dataset during day time travel

global_param_dict = {}
global_param_dict['Year_param_emit'] = Year_param_emit
global_param_dict['Hour_param_emit'] = Hour_param_emit
global_param_dict['FF_Condition'] = FF_Condition
global_param_dict['points_threshold'] = points_threshold
global_param_dict['criteria'] = criteria

print('\033[1m' +"Hours to exclude for day time travel:" )
print(*Hour_param_emit, sep = ", ") 
print('\033[1m' +"Low volume(Free Flow) condition parameter Vol/lanes:" )
print(colored(FF_Condition,'blue')) 

print('\033[1m' +"Acceptable number of data points to calculate FF_SPD:" )
print(colored(points_threshold,'blue')) 

print('\033[1m' +"Criteria for acceptable segment result:" )
print(colored(criteria,'blue')) 

Hours to exclude for day time travel:
0, 1, 2, 3, 4, 19, 21, 22, 23
Low volume(Free Flow) condition parameter Vol/lanes:
500
Acceptable number of data points to calculate FF_SPD:
100
Criteria for acceptable segment result:
adj_R2 > 0.6 & RMSE < 10


## A2. Data input
### The raw data has been processed through ETL process, and performed quality control and reasonableness check

In [3]:
table_HV_hr = pd.read_table('input\\hv\\volumedata_0424.csv',sep=',') ## this table contains vehicle classification for traffic count data
table_attr = pd.read_table('input\\LINKID_ATTR_processed.csv',sep=',') ## this table contains road segment attribute data
speed_counter = pd.read_table('output_With_spd.csv', sep=',') ## this table contains the joined view of traffic volume and speed data for each segment 

## A3. Data cleaning and formatting

###  traffic count and speed

In [4]:
# Add several columns to the 'speed_counter' DataFrame with fixed values
speed_counter['LINK_CAP'] = 2300
speed_counter['JURISDICTION'] = 99
speed_counter['RTE_NUMBER'] = 99
# Rename some columns in 'speed_counter' and drop unnecessary columns to create a new DataFrame called 'hourly_vol_spd_melt'
hourly_vol_spd_melt = speed_counter.rename(columns={"Hour": "hour","TotalVol":"vol","AvgSpd":"speed","Year":"MY_YEAR","Mon":"MY_MONTH","Day":"MY_DAY"})
hourly_vol_spd_melt['Date'] = hourly_vol_spd_melt['MY_YEAR']*10000 + hourly_vol_spd_melt['MY_MONTH']*100 + hourly_vol_spd_melt['MY_DAY']
hourly_vol_spd_melt['Date'] = hourly_vol_spd_melt['Date'].astype(int)
hourly_vol_spd_melt.drop('Unnamed: 0', inplace=True, axis=1)
hourly_vol_spd_melt.drop('level_0', inplace=True, axis=1)
hourly_vol_spd_melt.drop('index', inplace=True, axis=1)
hourly_vol_spd_melt = hourly_vol_spd_melt[['LINKID', 'Date', 'hour', 'vol', 'speed', 'MY_YEAR', 'MY_MONTH', 'MY_DAY']]


In [5]:
print("hourly_vol_spd_melt should include data and follow structure as below, date 99-99 indicates only annual average data available")
hourly_vol_spd_melt.head()

hourly_vol_spd_melt should include data and follow structure as below, date 99-99 indicates only annual average data available


LINKID      Date  hour    vol      speed  MY_YEAR  MY_MONTH  MY_DAY
0   10005  20179999   0.0  402.0  63.320442   2017.0      99.0    99.0
1   10005  20179999   1.0  335.0  63.052055   2017.0      99.0    99.0
2   10005  20179999   2.0  295.0  62.975000   2017.0      99.0    99.0
3   10005  20179999   3.0  282.0  62.911846   2017.0      99.0    99.0
4   10005  20179999   4.0  324.0  62.891667   2017.0      99.0    99.0

### Heavy vechile percent calculation

In [6]:
print("table_HV_hr should include data and follow structure as below")
table_HV_hr.head()

table_HV_hr should include data and follow structure as below


080122  01/01/2017 00:00  E  1  1,2  1.1  22  6  0  0.1  ...  0.2  0.3  5  \
0   80122  01/01/2017 01:00  E  1  1,2    0  13  5  0    0  ...    0    0  2   
1   80122  01/01/2017 02:00  E  1  1,2    0  10  3  0    0  ...    0    0  5   
2   80122  01/01/2017 03:00  E  1  1,2    0  11  1  0    0  ...    0    0  2   
3   80122  01/01/2017 04:00  E  1  1,2    0  16  3  0    1  ...    0    0  3   
4   80122  01/01/2017 05:00  E  1  1,2    0  12  2  0    0  ...    0    0  8   

   0.4  0.5  0.6  0.7  0.8  35  4  
0    0    0    0    0    0  20  4  
1    0    0    0    0    0  18  4  
2    0    0    0    0    0  14  4  
3    0    0    0    0    0  23  4  
4    0    0    0    0    0  22  4  

[5 rows x 21 columns]

In [7]:
pd.set_option('display.max_columns', None)
# Rename columns in the 'table_HV_hr' DataFrame
table_HV_hr.columns = ['LINKID', 'Date_Time','DIRECTION','COUNTERNUMBER','MAX(LANENUMBER)','SUM(VEHICLECLASS01)','SUM(VEHICLECLASS02)','SUM(VEHICLECLASS03)','SUM(VEHICLECLASS04)','SUM(VEHICLECLASS05)','SUM(VEHICLECLASS06)','SUM(VEHICLECLASS07)','SUM(VEHICLECLASS08)','SUM(VEHICLECLASS09)','SUM(VEHICLECLASS10)','SUM(VEHICLECLASS11)','SUM(VEHICLECLASS12)','SUM(VEHICLECLASS13)','SUM(VEHICLECLASS14)','SUM(VEHICLECLASS15)','RAWDATAQUALITY']
# Convert the 'Date_Time' column to a datetime object in 'table_HV_hr'
table_HV_hr['DT_formatted'] = pd.to_datetime(table_HV_hr['Date_Time'])
table_HV_hr['MY_YEAR'] = table_HV_hr['DT_formatted'].dt.year
table_HV_hr['MY_MONTH'] = table_HV_hr['DT_formatted'].dt.month
table_HV_hr['MY_DATE'] = table_HV_hr['DT_formatted'].dt.date
table_HV_hr['MY_HOUR'] = table_HV_hr['DT_formatted'].dt.hour
# Concatenate the 'MY_YEAR', 'MY_MONTH', and 'MY_DATE' columns into a new column called 'Date'
table_HV_hr["Date"] = table_HV_hr["DT_formatted"].dt.strftime('%Y%m%d')
table_HV_hr['Date'] = pd.to_numeric(table_HV_hr['Date'])
# Rename the 'MY_HOUR' column to 'hour' and the 'MAX(LANENUMBER)' column to 'Lane_num_HV'
table_HV_hr = table_HV_hr.rename(columns={"MY_HOUR": "hour", "MAX(LANENUMBER)": "Lane_num_HV"})
# Extract the maximum number of lanes from the 'MAX(LANENUMBER)' column and update the 'Lane_num_HV' column
table_HV_hr['Lane_num_HV'] = table_HV_hr['Lane_num_HV'].str.split(',').apply(lambda x: max(map(int, x)))

# Calculate the total number of vehicles and heavy vehicles and the percentage of heavy vehicles for each row in 'table_HV_hr'
table_HV_hr['total_veh'] = table_HV_hr['SUM(VEHICLECLASS01)']+\
                            table_HV_hr['SUM(VEHICLECLASS02)']+\
                            table_HV_hr['SUM(VEHICLECLASS03)']+\
                            table_HV_hr['SUM(VEHICLECLASS04)']+\
                            table_HV_hr['SUM(VEHICLECLASS05)']+\
                            table_HV_hr['SUM(VEHICLECLASS06)']+\
                            table_HV_hr['SUM(VEHICLECLASS07)']+\
                            table_HV_hr['SUM(VEHICLECLASS08)']+\
                            table_HV_hr['SUM(VEHICLECLASS09)']+\
                            table_HV_hr['SUM(VEHICLECLASS10)']+\
                            table_HV_hr['SUM(VEHICLECLASS11)']+\
                            table_HV_hr['SUM(VEHICLECLASS12)']+\
                            table_HV_hr['SUM(VEHICLECLASS12)']+\
                            table_HV_hr['SUM(VEHICLECLASS13)']+\
                            table_HV_hr['SUM(VEHICLECLASS14)']+\
                            table_HV_hr['SUM(VEHICLECLASS15)']

table_HV_hr['heavy_veh'] = table_HV_hr['SUM(VEHICLECLASS04)']+\
                            table_HV_hr['SUM(VEHICLECLASS05)']+\
                            table_HV_hr['SUM(VEHICLECLASS06)']+\
                            table_HV_hr['SUM(VEHICLECLASS07)']+\
                            table_HV_hr['SUM(VEHICLECLASS08)']+\
                            table_HV_hr['SUM(VEHICLECLASS09)']+\
                            table_HV_hr['SUM(VEHICLECLASS10)']+\
                            table_HV_hr['SUM(VEHICLECLASS11)']+\
                            table_HV_hr['SUM(VEHICLECLASS12)']+\
                            table_HV_hr['SUM(VEHICLECLASS13)']
table_HV_hr['hr_hv_pct'] = table_HV_hr['heavy_veh']/table_HV_hr['total_veh']*100
# Calculate the mean value of the 'PERCENT_HV' column in 'table_HV_yr'
hvpct_param = table_HV_hr["hr_hv_pct"].mean()
# Print a message to the console that includes the average value of 'PERCENT_HV' with formatting
print('\033[1m' + "Average HV pct of all available segments:", colored("%0.2f" % hvpct_param, 'blue'))

Average HV pct of all available segments: 8.23


For more details about __FF_condition__, see [FF_Condition usage](#FF_Condition). 

For more details about __points_threshold__, see [points_threshold usage](#points_threshold). 

For more details about __criteria__, see [criteria](#criteria).

# B. Join Attribute data with hourly speed&volume matrix by LINKID
### In this section, multiple attribute tables will be joined to the speed&volume data
1. Post speed, Lane number
2. Heavy vehicle percentage information

## B.1. Joined view of vol_spd and Lane number and Post Speed

In [8]:
# Merge two pandas DataFrames, 'hourly_vol_spd_melt' and 'table_attr', on the 'LINKID' column
hourly_vol_spd_melt_attr = pd.merge(hourly_vol_spd_melt, table_attr, how='left', left_on=['LINKID'], right_on=['LINKID'])
# Print the first few rows of the merged DataFrame
hourly_vol_spd_melt_attr.head()

LINKID      Date  hour    vol      speed  MY_YEAR  MY_MONTH  MY_DAY  TMC  \
0   10005  20179999   0.0  402.0  63.320442   2017.0      99.0    99.0  NaN   
1   10005  20179999   1.0  335.0  63.052055   2017.0      99.0    99.0  NaN   
2   10005  20179999   2.0  295.0  62.975000   2017.0      99.0    99.0  NaN   
3   10005  20179999   3.0  282.0  62.911846   2017.0      99.0    99.0  NaN   
4   10005  20179999   4.0  324.0  62.891667   2017.0      99.0    99.0  NaN   

   LANE_NUM  POST_SPD  LINK_CAP  
0       NaN       NaN       NaN  
1       NaN       NaN       NaN  
2       NaN       NaN       NaN  
3       NaN       NaN       NaN  
4       NaN       NaN       NaN

## B.2. Heavy Vehicle Percent fill
### There are two sets of vehicle class composition data, one is hourly but less coverage, the other is yearly with better coverage
1) Fill the HV_PCT with yearly hourly first(no LINKID)

2) Then fill with yearly hourly available data(with LINKID)

3) Lastly fill with daily hourly available data(with LINKID)

### 1) Fill Year-Hour average for all LINKID

In [9]:
# Group by year and hour, compute average of table_HV_hr column
table_HV_fill_1 =  table_HV_hr[['MY_YEAR', 'hour','Lane_num_HV', 'hr_hv_pct']].groupby(['MY_YEAR','hour']).agg({'Lane_num_HV':'mean', 'hr_hv_pct':'mean'}).reset_index()
# Merge two pandas DataFrames, 'hourly_vol_spd_melt_attr' and 'table_HV_yr', on the 'LINKID' and 'MY_YEAR' columns
hourly_vol_spd_melt_hv = pd.merge(hourly_vol_spd_melt_attr, table_HV_fill_1, how='left', left_on=['MY_YEAR','hour'], right_on=['MY_YEAR','hour'])
hourly_vol_spd_melt_hv['PERCENT_HV'] = hourly_vol_spd_melt_hv['hr_hv_pct']
hourly_vol_spd_melt_hv = hourly_vol_spd_melt_hv.drop('hr_hv_pct', axis=1)

### 2) Fill LINKID YEAR-Hour Hv_Pct value

In [10]:
table_HV_fill_2 = table_HV_hr[['LINKID', 'MY_YEAR', 'hour','Lane_num_HV', 'hr_hv_pct']].groupby(['LINKID', 'MY_YEAR', 'hour']).agg({'Lane_num_HV':'mean', 'hr_hv_pct':'mean'}).reset_index()
hourly_vol_spd_melt_hv = pd.merge(hourly_vol_spd_melt_hv, table_HV_fill_2, how='left', left_on=['LINKID','MY_YEAR','hour'], right_on=['LINKID','MY_YEAR','hour'])
hourly_vol_spd_melt_hv['hr_hv_pct'].fillna(hourly_vol_spd_melt_hv['PERCENT_HV'],inplace=True)
hourly_vol_spd_melt_hv['PERCENT_HV'] = hourly_vol_spd_melt_hv['hr_hv_pct']
hourly_vol_spd_melt_hv = hourly_vol_spd_melt_hv.drop('hr_hv_pct', axis=1)

### 3) Fill LINKID Date Hour Hv_Pct value

In [11]:
table_HV_fill_3 = table_HV_hr[['LINKID', 'Date', 'hour','Lane_num_HV', 'hr_hv_pct']].groupby(['LINKID', 'Date', 'hour']).agg({'Lane_num_HV':'mean', 'hr_hv_pct':'mean'}).reset_index()
hourly_vol_spd_melt_hv = pd.merge(hourly_vol_spd_melt_hv, table_HV_fill_3, how='left', left_on=['LINKID','Date','hour'], right_on=['LINKID','Date','hour'])
hourly_vol_spd_melt_hv['hr_hv_pct'].fillna(hourly_vol_spd_melt_hv['PERCENT_HV'],inplace=True)
hourly_vol_spd_melt_hv['PERCENT_HV'] = hourly_vol_spd_melt_hv['hr_hv_pct']
hourly_vol_spd_melt_hv = hourly_vol_spd_melt_hv.drop('hr_hv_pct', axis=1)

In [12]:
hourly_vol_spd_melt_hv = hourly_vol_spd_melt_hv[['LINKID','POST_SPD','LANE_NUM','MY_YEAR','Date','hour','vol','speed','PERCENT_HV']].dropna()

In [13]:
print("Number of segments with available vol&spd w/ attribute:" , colored(len(hourly_vol_spd_melt_hv.LINKID.unique()),'blue'))

Number of segments with available vol&spd w/ attribute: 758


In [14]:
linkid_available = list(hourly_vol_spd_melt_attr.LINKID.unique())
hourly_vol_spd_melt_attr[(hourly_vol_spd_melt_attr["LINKID"]==linkid_available[0])].head()

LINKID      Date  hour    vol      speed  MY_YEAR  MY_MONTH  MY_DAY  TMC  \
0   10005  20179999   0.0  402.0  63.320442   2017.0      99.0    99.0  NaN   
1   10005  20179999   1.0  335.0  63.052055   2017.0      99.0    99.0  NaN   
2   10005  20179999   2.0  295.0  62.975000   2017.0      99.0    99.0  NaN   
3   10005  20179999   3.0  282.0  62.911846   2017.0      99.0    99.0  NaN   
4   10005  20179999   4.0  324.0  62.891667   2017.0      99.0    99.0  NaN   

   LANE_NUM  POST_SPD  LINK_CAP  
0       NaN       NaN       NaN  
1       NaN       NaN       NaN  
2       NaN       NaN       NaN  
3       NaN       NaN       NaN  
4       NaN       NaN       NaN

# C. Create testing and validation dataset from available segments
### Omit segments with __low data coverage__ , the riria is set to 200 datapoints
### Use __80%-20% ratio__ to randomly create testing and validation set



In [15]:
# Create two new empty DataFrames, 'testing' and 'validating'
testing = pd.DataFrame()
validating = pd.DataFrame()

# Create an empty list to store records that are omitted due to having too few rows in the training set
omit_record = []

# Iterate through the unique values of 'LINKID' in 'hourly_vol_spd_melt_hv'
for LINKID in hourly_vol_spd_melt_hv['LINKID'].unique():
    # Subset the rows of 'hourly_vol_spd_melt_hv' that have the current 'LINKID'
    subset_raw_0 = hourly_vol_spd_melt_hv[hourly_vol_spd_melt_hv['LINKID'] == LINKID]
    
    # Filter out rows with 'hour' values that are in 'Hour_param_emit'
    subset_raw_1 = subset_raw_0[~subset_raw_0['hour'].isin(Hour_param_emit)]
    
    # Filter out rows with 'MY_YEAR' values that are in 'Year_param_emit'
    subset_raw = subset_raw_1[~subset_raw_1['MY_YEAR'].isin(Year_param_emit)]
    
    # Split the remaining rows into training and validation sets using 'sample()' method and a 80/20 split
    testing_iter = subset_raw.sample(frac=0.8)
    validating_iter = subset_raw.drop(testing_iter.index)

    # If the number of rows in the training set is greater than 150, append it to 'testing' and 'validating'
    if len(testing_iter) > 40:
        testing = pd.concat([testing, testing_iter])
        validating = pd.concat([validating, validating_iter])
    # Otherwise, record the 'LINKID' and the number of rows in the training set in 'omit_record'
    else:
        omit_record.append([LINKID, len(testing_iter)])

# Reset the index of 'testing' and 'validating'
testing = testing.reset_index()
validating = validating.reset_index()

# Write 'testing' and 'validating' DataFrames to separate CSV files
testing.to_csv(r'BPR_testing_set.csv', index=False) 
validating.to_csv(r'BPR_validating_set.csv', index=False)


In [16]:
print("Number of segments with available vol&spd w/ attribute:" , colored(len(hourly_vol_spd_melt_hv.LINKID.unique()),'blue'))
print("Number of segments filtered for testing:" ,colored(len(testing.LINKID.unique()),'blue'))

Number of segments with available vol&spd w/ attribute: 758
Number of segments filtered for testing: 750


In [17]:
print("LINKIDs that does not have enough data coverage")
pd.DataFrame(omit_record, columns=['LINKID', 'count']).head()

LINKIDs that does not have enough data coverage


LINKID  count
0  190071     24
1  190072     24
2  190074     24
3  190075     24
4  190077     23

# D. Create curve fitting model and rules to improve the result 
 Data filtering and outlier omit
1. Estimate free flow speed with low volume(free flow) condition
2. Filter out over congested condition using density

 Model process

3. Calculate values for volume delay function x and y
4. Define Volume Delay Function and estimate the parameters
5. Calculate RMSE and Adjusted R square for goodness of fit

In [18]:
import numpy as np
import os
import copy
import matplotlib.pyplot as plt
import math
import statistics
from scipy.optimize import curve_fit
import matplotlib.pyplot as plt
import pandas as pd
from random import sample
from pylab import *
from scipy.optimize import curve_fit
from scipy import stats
import gc

del testing
del validating
gc.collect()

16

In [19]:
testing = pd.read_table('BPR_testing_set.csv',sep=',')
validating = pd.read_table('BPR_validating_set.csv',sep=',')

<a id='FF_Condition'></a>
<a id='points_threshold'></a>



### D.1. Estimate __free flow speed__ with __low volume(free flow) condition__

In [20]:
# Create a new column called 'VoverLns' in the 'testing' DataFrame
# The values in the new column are calculated by dividing the 'vol' column by the 'LANE_NUM' column
testing['VoverLns'] = testing['vol'] / testing['LANE_NUM']

In [21]:
# Calculate FFSPD for each LINKID based on the available data
LINKID_unique = testing['LINKID'].unique()

for LINKID in LINKID_unique:
    # Subset the data for each LINKID
    subset = testing[testing['LINKID'] == LINKID]
    
    # Calculate the average post speed for this LINKID
    postspd = subset['POST_SPD'].mean()
    
    # Filter for low volume, high speed condition
    free_flow_set = subset.query('VoverLns < @FF_Condition and speed >= POST_SPD')
    
    # If enough data points are available for the low volume, high speed condition
    if len(free_flow_set) > points_threshold:
        # Calculate the average speed of the low volume condition
        ffspd = free_flow_set.speed.mean()
        # If the low volume condition's average speed is less than post speed,
        # flag that the postspeed may need to be double-checked
        if ffspd < postspd:
            FFSPD_indicator = 'Yes, double check Postspeed'
            ffspd = postspd + ffspd_offset
        else:
            FFSPD_indicator = 'Yes'
    else:
        # If there are not enough data points for the low volume condition,
        # calculate FFSPD as postspeed + a constant offset
        ffspd = postspd + ffspd_offset
        FFSPD_indicator = 'No'
        
    # Get the maximum speed value in the subset
    spdmax = subset['speed'].max()
    
    # Assign FFSPD, FFSPD total data, and FFSPD indicator to the corresponding LINKID rows in the testing and validating dataframes
    testing.loc[testing['LINKID'] == LINKID, ['FFSPD']] = ffspd
    validating.loc[validating['LINKID'] == LINKID, ['FFSPD']] = ffspd
    testing.loc[testing['LINKID'] == LINKID, ['FFSPD_total_data']] = len(free_flow_set)
    testing.loc[testing['LINKID'] == LINKID, ['FFSPD_from_spd_quantile']] = FFSPD_indicator
    validating.loc[validating['LINKID'] == LINKID, ['FFSPD_from_spd_quantile']] = FFSPD_indicator

    
if len(testing.query('FFSPD_from_spd_quantile == "Yes, double check Postspeed"')[['LINKID','FFSPD','FFSPD_total_data','POST_SPD']].drop_duplicates().LINKID.unique())> 0:
    print(colored('\033[1m' + "Attention: LINKID with FFSpd < POST_SPD",'red'))
    print(len(testing.query('FFSPD_from_spd_quantile == "Yes, double check Postspeed"')[['LINKID','FFSPD','FFSPD_total_data','POST_SPD']].drop_duplicates().LINKID.unique()))
    # print(testing.query('FFSPD_from_spd_quantile == "Yes, double check Postspeed"')[['LINKID','FFSPD','FFSPD_total_data','POST_SPD']].drop_duplicates())
else:
    print(colored("No FFSPD inconsistency",'green') )
    
print(colored('\033[1m' + "Total Links passing minimum coverage datapoints",'green'), len(testing.query('FFSPD_from_spd_quantile == "Yes"')[['LINKID','FFSPD','FFSPD_total_data','POST_SPD']].drop_duplicates().LINKID.unique()),
      colored('\n\033[1m' + "Links with FFSPD_from_data < POST_SPD",'red'), len(testing.query('FFSPD_from_spd_quantile == "Yes, double check Postspeed"')[['LINKID','FFSPD','FFSPD_total_data','POST_SPD']].drop_duplicates().LINKID.unique()),
      colored('\n\033[1m' + "Total Links does not have minimum coverage datapoints",'yellow'), len(testing.query('FFSPD_from_spd_quantile == "No"')[['LINKID','FFSPD','FFSPD_total_data','POST_SPD']].drop_duplicates().LINKID.unique()))

No FFSPD inconsistency
Total Links passing minimum coverage datapoints 362 
Links with FFSPD_from_data < POST_SPD 0 
Total Links does not have minimum coverage datapoints 388


<a id='critical_cong_param'></a>

### D.2. Filter out __over congested condition__ using the Density

In [22]:
# Calculating and filtering by density
testing['density'] = testing['vol']/testing['speed']/testing['LANE_NUM'] # Calculate density
float_format = "{:.2f}".format
testing['density'].describe().apply(float_format) # Display density statistics
testing = testing.query('density <45') # Filter rows where density is less than 45

validating['density'] = validating['vol']/validating['speed']/validating['LANE_NUM'] # Calculate density
float_format = "{:.2f}".format
validating['density'].describe().apply(float_format) # Display density statistics
validating = validating.query('density < 45') # Filter rows where density is less than 45

index_names = testing[(testing['speed'] <= 0.7*testing['FFSPD'])].index
# drop these given row
# indexes from dataFrame
testing.drop(index_names, inplace = True)

index_names = validating[(validating['speed'] <= 0.7*validating['FFSPD'])].index
# drop these given row
# indexes from dataFrame
validating.drop(index_names, inplace = True)


# Iterate through LINKIDs in testing set
LINKID_unique =  testing['LINKID'].unique()
for LINKID in LINKID_unique:
    subset = testing[testing["LINKID"]==LINKID] # Subset testing data for current LINKID
    
    postspd = subset['POST_SPD'].mean() # Calculate average post speed for subset
    
    cong_flow_set = subset[(subset['VoverLns'] > 1000)] # Subset for congested flow based on V/L > 1000

    testing.loc[testing['LINKID']==LINKID, "Cong_total_data"] = len(cong_flow_set) # Add number of congested flow data points to testing DataFrame
    testing.loc[testing['LINKID']==LINKID, "total_data"] = len(subset) # Add total number of data points to testing DataFrame
    
## Some LINKIDs are missing LANE_NUM info, the density is null, which is excluded from the testing set
print(len(testing['LINKID'].unique())) # Print number of unique LINKIDs in testing DataFrame


750


### D.3. Calculate values for volume delay function __x(V/C Ratio)__ and __y(T over T0)__
1) Calculate Free Flow Capacity using the estimated Free Flow Speed 

2) Calculate the Capacity with Heavy Vehicle percentage based on the HCM formula

3) Calculate V/C ratio and T over T0(Free flow speed over speed)

In [23]:
testing['VoverLns'] = testing['vol'] / testing['LANE_NUM']  # Calculate volume over lanes
testing['Cap_FFS'] = np.where(testing['FFSPD'] < 70, 2200+10*(testing['FFSPD'] -50), 2400)  # Calculate capacity of facility at free-flow speed
testing['Cap_HV'] = testing['Cap_FFS']/(1+testing['PERCENT_HV']/100)  # Calculate capacity of facility with heavy vehicle adjustment
testing['VoverC'] = testing['VoverLns'] / testing['Cap_HV']  # Calculate the volume to capacity ratio
testing['ToverT0'] = testing['FFSPD'] / testing['speed']  # Calculate travel time ratio at free-flow speed
testing['ToverT0'] = np.where(testing['ToverT0'] < 1, 1,testing['ToverT0'])  # Set minimum value of travel time ratio to 1

# Calculate y_std variable for each LINKID
LINKID_unique =  testing['LINKID'].unique()
for LINKID in LINKID_unique:
    subset = testing[testing["LINKID"]==LINKID]  # Subset data for a specific LINKID
    y_std = subset['ToverT0'].std()  # Calculate the standard deviation of the travel time ratio
    testing.loc[testing['LINKID']==LINKID, ['y_std']] = y_std  # Assign the y_std value to all rows for that LINKID


In [24]:
validating['VoverLns'] = validating['vol'] / validating['LANE_NUM'] # compute volume over number of lanes
validating['Cap_FFS'] = np.where(validating['FFSPD'] < 70, 2200+10*(validating['FFSPD'] -50), 2400) # compute capacity at free flow speed
validating['Cap_HV'] = validating['Cap_FFS']/(1+validating['PERCENT_HV']/100) # compute capacity with heavy vehicle adjustment
validating['VoverC'] = validating['VoverLns'] / validating['Cap_HV'] # compute volume-to-capacity ratio

In [25]:
validating.to_csv(r'BPR_validating_set.csv', index=False) 
Cap_override = pd.read_table('input\LINKID_Cap.csv',sep=',')

In [26]:
# Merge Cap_override dataframe with validating dataframe based on LINKID
temp_df = pd.merge(validating, Cap_override,  how='left', left_on=['LINKID'], right_on =['LINKID'])

# Drop Cap_HV column from validating and rename Cap column from Cap_override to Cap_HV
temp_df = temp_df.drop(['Cap_HV'], axis=1)
temp_df = temp_df.rename(columns={'Cap': 'Cap_HV'})

# Recalculate VoverC column in validating based on updated Cap_HV values
temp_df['VoverC'] = temp_df['VoverLns'] / temp_df['Cap_HV']
validating = temp_df

In [27]:
# Merge Cap_override dataframe with testing dataframe based on LINKID
temp_df = pd.merge(testing, Cap_override,  how='left', left_on=['LINKID'], right_on =['LINKID'])

# Drop Cap_HV column from temp_df and rename Cap column as Cap_HV
temp_df = temp_df.drop(['Cap_HV'], axis=1)
temp_df = temp_df.rename(columns={'Cap': 'Cap_HV'})

# Calculate VoverC by dividing VoverLns by Cap_HV in temp_df
temp_df['VoverC'] = temp_df['VoverLns'] / temp_df['Cap_HV']

# Assign updated testing dataframe to temp_df
testing = temp_df


In [28]:
import gc
del temp_df
gc.collect()

112

### D.4. Define Volume Delay Function and estimate the parameters

In [29]:
## To address the imbalance in the current dataset, particularly in low volume conditions, 
## we have implemented a method to better capture the impact of increased traffic volume on speed reduction. 
## This involves a manual selection of data points within various Volume-to-Capacity (V/C) ratio bins. 
## Please note that this step can be omitted if the data distribution becomes more uniform.

# Define the number of bins to use and the interval between each bin
xbins = 20
interval = 1/xbins
bins = np.arange(0,1.05,0.05)

# Create an empty dataframe to hold the samples
df_sample_new = pd.DataFrame()

# Loop through each unique LINKID in the dataset
for LINKID in LINKID_unique:
    
    # Subset the dataset to only include rows with the current LINKID
    sample = testing[testing["LINKID"]==LINKID]
    
    # Bin the data based on VoverC and count the number of samples in each bin
    sample["bin"] = pd.cut(sample['VoverC'], bins=bins)
    bin_counts = sample.groupby('bin').size()
    
    # Loop through each bin and select a sample of data to add to the new dataframe
    for i in range(xbins):
        
        # Subset the data to only include samples in the current bin
        subset = sample.query('VoverC>@i*@interval & VoverC<=(@i+1)*@interval')
        
        # Set the sample size based on the bin number and size of the bin
        if i+1 < 5 and len(subset) > sample_size:
            subset_sample = subset.sample(n=sample_size)
        elif i+1 < 10 and len(subset) > 2 * sample_size:
            subset_sample = subset.sample(n=2 * sample_size)
        elif i+1 >= 10:
            if len(subset) > 4 * sample_size:
                subset_sample = subset.sample(n= 4 * sample_size)
            else:
                subset_sample = subset
        else:
            subset_sample = pd.DataFrame()
        
        # Add the subset sample to the new dataframe
        if len(subset_sample) > 0:
            df_sample_new = pd.concat([df_sample_new, subset_sample])
selection = df_sample_new.groupby('LINKID').size().reset_index(name='count').LINKID.unique()
testing = df_sample_new.query('LINKID in @selection')

In [30]:
# Loop over unique LINKIDs in testing dataframe
for LINKID in LINKID_unique:
    # Get subset of testing dataframe where LINKID matches
    subset = testing[testing["LINKID"]==LINKID]
    # Calculate standard deviation of ToverT0 for this subset
    y_std = subset['ToverT0'].std()
    # Update y_std column in testing dataframe where LINKID matches
    testing.loc[testing['LINKID']==LINKID, ['y_std']] = y_std
testing = testing.query('y_std>0')

In [31]:
# Define a function that models the speed-density relationship
def model_float(x,a,b):
    bpr = 1+a*np.power(x, b)
    return (bpr)

# Define a function that estimates the model parameters for each road segment
def Model_estimate(df):
    # Get the unique road segment IDs
    LINKID_unique =  df['LINKID'].unique()
    # Set the bounds for the BPR function parameters
    BPR_bound = [[0,1],[1,10]]
    # Loop over each road segment
    for LINKID in LINKID_unique:
        # Get the subset of data for the current road segment
        subset = df[df["LINKID"]==LINKID].query('VoverC>0 and ToverT0>0 and y_std>0')
        # Fit the BPR function to the data for the current road segment
        best_vals, covar = curve_fit(model_float, subset['VoverC'], subset['ToverT0'], sigma=subset['y_std'],
                                     bounds=((BPR_bound[0][0],BPR_bound[0][1]), (BPR_bound[1][0],BPR_bound[1][1])), maxfev=50000000)
        # Update the dataframe with the model parameters and predicted travel time
        subset['alpha_iter'] = best_vals[0] 
        subset['beta_iter'] = best_vals[1] 
        df.loc[df['LINKID']==LINKID, ['alpha_iter']] = best_vals[0] 
        df.loc[df['LINKID']==LINKID, ['beta_iter']] = best_vals[1] 
        df.loc[df['LINKID']==LINKID, ['model_t']] =  model_float(subset['VoverC'], subset['alpha_iter'], subset['beta_iter'])
    # Calculate the predicted speed based on the predicted travel time
    df['model_spd'] = df['FFSPD'] / df['model_t']
    return df

# Call the Model_estimate function with the testing data
testing = Model_estimate(testing)
# Print the number of unique road segment IDs in the testing data
print("total number of unique segments in testing set")
print(len(testing['LINKID'].unique()))


C:\windows\Anaconda3\lib\site-packages\scipy\optimize\minpack.py:833: OptimizeWarning:

Covariance of the parameters could not be estimated



total number of unique segments in testing set
620


### D.5. Calculate RMSE and Adjusted R square for goodness of fit

<a id='number_bins'></a>

In [32]:
def Calculate_Goodness_fit(df):
    # Get unique LINKIDs in the dataframe
    LINKID_unique = df['LINKID'].unique()
    
    # Loop through each LINKID
    for LINKID in LINKID_unique:
        
        # Calculate RMSE for the current LINKID
        subset = df[df["LINKID"] == LINKID]
        subset['res_spd'] = subset['model_spd'] - subset['speed']
        subset['sq_res_spd'] = np.power((subset['res_spd']), 2)
        mean_spd_sq = subset['sq_res_spd'].mean()
        SEOE = np.sqrt(mean_spd_sq)
        mean_Spd = subset['speed'].mean()
        RMSE_new = SEOE / mean_Spd * 100
        
        # Assign the RMSE and VoverLn_max to the dataframe for the current LINKID
        df.loc[df['LINKID'] == LINKID, ['RMSE']] = RMSE_new
        df.loc[df['LINKID'] == LINKID, ['VoverLn_max']] = subset['VoverLns'].max()
        
        # Calculate adjusted R-squared for the current LINKID
        model_spd_std = subset['model_spd'].std()
        obs_spd_std = subset['speed'].std()
        subset['model_spd_mean'] = subset['model_spd'].mean()
        subset['obs_spd_mean'] = subset['speed'].mean()
        subset['adj_R2_iter'] = (subset['speed'] - subset['obs_spd_mean']) * (subset['model_spd'] - subset['model_spd_mean'])
        n = len(subset['adj_R2_iter'])
        adj_R2 = subset['adj_R2_iter'].sum() / ((n - 1) * model_spd_std * obs_spd_std)
        
        # Assign the adjusted R-squared to the dataframe for the current LINKID
        df.loc[df['LINKID'] == LINKID, ['adj_R2']] = adj_R2
    
    return df

testing = Calculate_Goodness_fit(testing)
testing.to_csv(r'BPR_testing_result.csv', index=False) 
testing.head()

index  LINKID  POST_SPD  LANE_NUM  MY_YEAR      Date  hour     vol  \
115   1025   10181      70.0       2.0   2019.0  20199999  17.0  1730.0   
134   1000   10181      70.0       2.0   2018.0  20189999  16.0  1668.0   
136   1024   10181      70.0       2.0   2019.0  20199999  16.0  1755.0   
139   1001   10181      70.0       2.0   2018.0  20189999  17.0  1653.0   
140   1072   10181      70.0       2.0   2021.0  20219999  16.0  1778.0   

         speed  PERCENT_HV  VoverLns  FFSPD  FFSPD_total_data  \
115  69.862637    7.836955     865.0   77.0               4.0   
134  67.786111    8.488887     834.0   77.0               4.0   
136  69.708791    8.606545     877.5   77.0               4.0   
139  67.502793    7.712900     826.5   77.0               4.0   
140  68.977273    8.987895     889.0   77.0               4.0   

    FFSPD_from_spd_quantile    density  Cong_total_data  total_data  Cap_FFS  \
115                      No  12.381439              0.0        60.0   2400.0   
134                      No  12.303405              0.0        60.0   2400.0   
136                      No  12.588082              0.0        60.0   2400.0   
139                      No  12.243938              0.0        60.0   2400.0   
140                      No  12.888303              0.0        60.0   2400.0   

       VoverC   ToverT0     y_std  Cap_HV          bin  alpha_iter  beta_iter  \
115  0.480556  1.102163  0.023561    1800  (0.45, 0.5]    0.262019        1.0   
134  0.463333  1.135926  0.023561    1800  (0.45, 0.5]    0.262019        1.0   
136  0.487500  1.104595  0.023561    1800  (0.45, 0.5]    0.262019        1.0   
139  0.459167  1.140694  0.023561    1800  (0.45, 0.5]    0.262019        1.0   
140  0.493889  1.116310  0.023561    1800  (0.45, 0.5]    0.262019        1.0   

      model_t  model_spd      RMSE  VoverLn_max    adj_R2  
115  1.125915  68.388833  2.066221        889.0 -0.256888  
134  1.121402  68.664031  2.066221        889.0 -0.256888  
136  1.127734  68.278488  2.066221        889.0 -0.256888  
139  1.120311  68.730945  2.066221        889.0 -0.256888  
140  1.129408  68.177286  2.066221        889.0 -0.256888

In [33]:
lookup_cols = ["LINKID","alpha_iter","beta_iter","Cap_FFS","FFSPD","POST_SPD","LANE_NUM"]
lookup_set = testing[lookup_cols].drop_duplicates()
lookup_set

LINKID  alpha_iter  beta_iter      Cap_FFS      FFSPD  POST_SPD  \
115       10181    0.262019   1.000000  2400.000000  77.000000      70.0   
180       10182    0.325244   1.000000  2400.000000  77.000000      70.0   
14019     10187    0.070575   1.000000  2400.000000  70.808496      70.0   
35638     10189    0.300300   1.000000  2400.000000  77.000000      70.0   
48263     10332    0.776460   5.874278  2400.000000  70.934351      70.0   
...         ...         ...        ...          ...        ...       ...   
7726049  940420    0.010724   1.000000  2384.142035  68.414204      65.0   
7746894  940726    0.017224   1.000000  2400.000000  72.386641      70.0   
7772243  970311    0.244523   4.930530  2400.000000  73.917145      70.0   
7796519  980300    0.028416   1.000000  2400.000000  71.834471      70.0   
7799017  980503    0.405021   5.117042  2400.000000  72.182865      65.0   

         LANE_NUM  
115           2.0  
180           2.0  
14019         2.0  
35638         3.0  
48263         2.0  
...           ...  
7726049       3.0  
7746894       2.0  
7772243       2.0  
7796519       2.0  
7799017       2.0  

[620 rows x 7 columns]

In [34]:
# Import plotly express library
import plotly.express as px

# Set the LINKID to visualize
LINKID = 90272

# Select the data for the specified LINKID
subset_plot = testing[testing["LINKID"]==LINKID]

# Convert MY_YEAR column to string
subset_plot["MY_YEAR"] = subset_plot["MY_YEAR"].astype(str)

# Create scatter plot
fig = px.scatter(subset_plot, x="vol", y="speed", color='MY_YEAR', title="Example Volume Speed plot: LINKID "+str(LINKID))

# Set y-axis range
fig.update(layout_yaxis_range = [0,80])

# Set layout size
fig.update_layout(autosize=False, width=800, height=800)

# Display the plot
fig.show()


# E. Generating Overall Parameters and Validating
### This approach seeks to create an overall parameter that accurately represents the entire VA interstate.
### While individual regressions may perform better with higher-quality or more extensive data,
### this overall parameter serves as a valuable baseline representation.


<a id='criteria'></a>


In [35]:
validating = pd.read_table('BPR_validating_set.csv',sep=',')
validating.columns

Index(['index', 'LINKID', 'POST_SPD', 'LANE_NUM', 'MY_YEAR', 'Date', 'hour',
       'vol', 'speed', 'PERCENT_HV', 'FFSPD', 'FFSPD_from_spd_quantile',
       'density', 'VoverLns', 'Cap_FFS', 'Cap_HV', 'VoverC'],
      dtype='object')

In [36]:
# Calculate essential fields for validation dataset
validating = pd.read_table('BPR_validating_set.csv',sep=',')
validating_temp = pd.DataFrame() 
LINKID_unique =  list(validating['LINKID'].unique())
for LINKID in LINKID_unique:
        subset = validating[validating["LINKID"]==LINKID]
        lookup_subset = lookup_set[lookup_set['LINKID']==LINKID]
        if not lookup_subset.empty:
        # Extract the Cap_FFS and FFSPD values from the lookup_subset dataset
            Cap_FFS = float(lookup_subset['Cap_FFS'])
            FFSPD = float(lookup_subset['FFSPD'])
            subset['Cap_FFS'] = Cap_FFS
            subset['Cap_HV'] = Cap_FFS/(1+subset['PERCENT_HV']/100)
            subset['FFSPD'] = FFSPD
            subset['VoverLns'] = subset['vol']/(subset['LANE_NUM'])
            subset['VoverC'] = subset['vol']/(subset['LANE_NUM']*subset['Cap_HV'])
            cong_flow_set = subset[(subset['VoverLns'] > 1000)]
            subset['Cong_total_data'] = len(cong_flow_set)
            subset['total_data'] = len(subset)
            validating_temp = pd.concat([validating_temp,subset], ignore_index=True)
validating =  validating_temp

In [37]:
# Use criteria parameter to filter the passing segment pool
plot_r2_select = testing.query(criteria)[['LINKID','alpha_iter','beta_iter','Cong_total_data','total_data','adj_R2','RMSE']].drop_duplicates().sort_values('LINKID').reset_index()
plot_r2_select = plot_r2_select.rename(columns={'alpha_iter': 'alpha', 'beta_iter': 'beta'})

In [38]:
plot_r2_select

index  LINKID     alpha       beta  Cong_total_data  total_data  \
0    802873   40099  1.000000   3.578529             28.0        60.0   
1    824090   40102  0.435805   2.245351             38.0        60.0   
2    824148   40104  0.340899   1.917944             33.0        60.0   
3   1035225   40290  0.505697   3.200222              2.0        60.0   
4   1142740   40302  0.483970   5.284844             47.0        60.0   
..      ...     ...       ...        ...              ...         ...   
75  7353115  190065  0.354036   5.570358             45.0        54.0   
76  7353313  190070  1.000000   3.187511              4.0        59.0   
77  7358406  190089  0.364376  10.000000             51.0        58.0   
78  7405684  190316  0.194178   3.450333          13037.0     17682.0   
79  7432743  199754  0.042139   3.185254             17.0        48.0   

      adj_R2      RMSE  
0   0.701185  3.668080  
1   0.714683  1.762209  
2   0.757119  0.963564  
3   0.640703  4.265145  
4   0.631640  4.503018  
..       ...       ...  
75  0.663145  5.910601  
76  0.791368  3.134296  
77  0.718342  7.371807  
78  0.608902  5.813131  
79  0.615978  4.340720  

[80 rows x 8 columns]

In [39]:
# Plot all passing segment VDF and get an average curve and VDF parameter
fig = make_subplots(rows=1, cols=3)

# Store all the individual VDF curves in y_record list
y_record = []
for i in range(len(plot_r2_select)):
    x = np.linspace(0, 1, 100)
    alpha = plot_r2_select.loc[i, 'alpha']
    beta = plot_r2_select.loc[i, 'beta']
    y_i = 1 + alpha * np.power(x, beta)
    y_record.append(y_i)
    fig.add_scatter(x=x, y=y_i, mode='lines', marker={'color': 'blue'}, row=1, col=1)

# Get the average VDF curve from y_record list
y_avg_list = [np.mean(k) for k in zip(*y_record)]
y_avg = np.array(y_avg_list)

# Plot the average VDF curve
fig.add_scatter(x=x, y=y_avg, mode='lines', marker={'color': 'red'}, row=1, col=3)

# Fit the average VDF curve to a BPR function and get the alpha and beta values
BPR_bound = [[0, 1], [1, 10]]
best_vals_avg, covar_avg = curve_fit(model_float, x, y_avg, bounds=((BPR_bound[0][0], BPR_bound[0][1]), (BPR_bound[1][0], BPR_bound[1][1])), maxfev=50000000)
alpha_overall = best_vals_avg[0]
beta_overall = best_vals_avg[1]

# Plot the BPR function with the alpha and beta values on the same plot as the average VDF curve
for i in range(len(plot_r2_select)):
    x = np.linspace(0, 2, 200)
    alpha = alpha_overall
    beta = beta_overall
    y_i = 1 + alpha * np.power(x, beta)
    fig.add_scatter(x=x, y=y_i, mode='lines', marker={'color': 'blue'}, row=1, col=2)
    x = np.linspace(0, 2, 200)
    alpha = 0.15
    beta = 4
    y_i = 1 + alpha * np.power(x, beta)
    fig.add_scatter(x=x, y=y_i, mode='lines', marker={'color': 'yellow'}, row=1, col=2)

# Apply the average VDF parameter and calculate goodness of fit
validating_result_avg = pd.DataFrame()
LINKID_unique = validating.LINKID.unique()

for LINKID in LINKID_unique:
    subset = validating[validating["LINKID"] == LINKID]
    alpha = best_vals_avg[0]
    beta = best_vals_avg[1]
    subset['alpha'] = alpha
    subset['beta'] = beta
    subset['ToverT0'] = model_float(subset['VoverC'], alpha, beta)
    subset['model_spd'] = subset['FFSPD'] / subset['ToverT0']
    validating_result_avg = pd.concat([validating_result_avg, subset], ignore_index=True)

validating_result_avg = Calculate_Goodness_fit(validating_result_avg)

# Print the results
print("Number of selected segments", len(plot_r2_select))
print("BPR Parameter" , "%.2f" %validating_result_avg.alpha.mean(),"%.2f" %validating_result_avg.beta.mean())
print("RMSE of Validating set" , "%.2f" %validating_result_avg[['LINKID','alpha','beta','adj_R2','RMSE']].drop_duplicates().reset_index().RMSE.mean())

# Show the plot
fig.show()

Number of selected segments 80
BPR Parameter 0.45 3.60
RMSE of Validating set 5.74


In [40]:
validating_result_avg.head()

index  LINKID  POST_SPD  LANE_NUM  MY_YEAR      Date  hour     vol  \
0    965   10181      70.0       2.0   2017.0  20179999   5.0   350.0   
1    969   10181      70.0       2.0   2017.0  20179999   9.0  1201.0   
2    976   10181      70.0       2.0   2017.0  20179999  16.0  1697.0   
3    992   10181      70.0       2.0   2018.0  20189999   8.0  1145.0   
4    993   10181      70.0       2.0   2018.0  20189999   9.0  1200.0   

       speed  PERCENT_HV  FFSPD FFSPD_from_spd_quantile    density  VoverLns  \
0  65.726027    9.753164   77.0                      No   2.662568     175.0   
1  66.447802    6.569617   77.0                      No   9.037169     600.5   
2  65.980822    4.821814   77.0                      No  12.859797     848.5   
3  67.166667   10.331964   77.0                      No   8.523573     572.5   
4  67.149171   10.787761   77.0                      No   8.935330     600.0   

   Cap_FFS       Cap_HV    VoverC  Cong_total_data  total_data     alpha  \
0   2400.0  2186.725106  0.080028                0          15  0.450518   
1   2400.0  2252.049012  0.266646                0          15  0.450518   
2   2400.0  2289.599757  0.370589                0          15  0.450518   
3   2400.0  2175.253578  0.263188                0          15  0.450518   
4   2400.0  2166.304282  0.276969                0          15  0.450518   

       beta   ToverT0  model_spd       RMSE  VoverLn_max    adj_R2  
0  3.596979  1.000051  76.996063  11.868001        870.0  0.023858  
1  3.596979  1.003880  76.702407  11.868001        870.0  0.023858  
2  3.596979  1.012677  76.036067  11.868001        870.0  0.023858  
3  3.596979  1.003702  76.716008  11.868001        870.0  0.023858  
4  3.596979  1.004448  76.659031  11.868001        870.0  0.023858

In [41]:
## Random select segments that Validation passes criteria

pool_for_fig = validating_result_avg.query('FFSPD_from_spd_quantile =="Yes" & adj_R2 > 0.5 & RMSE <10')[['LINKID','alpha','beta','adj_R2','RMSE']].drop_duplicates().reset_index().LINKID.to_numpy()

col = 3

select_LINKID = np.random.choice(pool_for_fig,col)

print (select_LINKID)
select_LINKID_str = ['%d' % x for x in select_LINKID]
fig = make_subplots(rows=1, cols=col,subplot_titles=(select_LINKID_str))

for i in range(col):
    LINKID = select_LINKID[i]
    subset_plot = validating_result_avg[validating_result_avg["LINKID"]==LINKID]
    subset_plot["MY_YEAR"] = subset_plot["MY_YEAR"].astype(str)
    RMSE = "{:.2f}".format(subset_plot["RMSE"].mean())
    adj_R2 = "{:.2f}".format(subset_plot["adj_R2"].mean())
    POST_SPD = "{:.2f}".format(subset_plot["POST_SPD"].mean())
    alpha = "{:.2f}".format(subset_plot["alpha"].mean())
    beta = "{:.2f}".format(subset_plot["beta"].mean())
    x_i = subset_plot["vol"].to_numpy() 
    y_i = subset_plot["speed"].to_numpy() 
    fig.add_trace(go.Scatter(x=x_i,y=y_i,mode='markers'),row=1, col=i+1)
    x = np.sort(subset_plot["vol"].to_numpy())
    y = np.sort(subset_plot["model_spd"].to_numpy())[::-1]
    fig.add_trace(go.Scatter(x=x, y=y,
                    mode='markers',
                    name='markers',
                    text="RMSE: " + str(RMSE) + "  adj_R2: " + str(adj_R2)+ "POST_SPD:" + str(POST_SPD) + "alpha:" + str(alpha) +"beta:" + str(beta)),
                    row=1, col=i+1)
    
    fig.update(layout_yaxis_range = [ 0,80])
    fig.update_layout( width=col * 400,   height=800,)
fig.show()
from IPython.display import display, HTML
js = "<script>$('.output_scroll').removeClass('output_scroll')</script>"
display(HTML(js))

[150126 140242  90138]
